<a href="https://colab.research.google.com/github/bylehn/auxetic_networks_jaxmd/blob/abhishek/test-auxetic.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import jax.numpy as np
import numpy as onp
from jax import random
from jax.config import config; config.update("jax_enable_x64", True)
from jax_md import space, energy, minimize, simulate, quantity
from jax import random, grad
from jax import jit
from jax import lax
import networkx as nx
from scipy.spatial import Delaunay
from scipy.spatial import ConvexHull
import matplotlib.pyplot as plt
from matplotlib import animation
import seaborn as sns
  
sns.set_style(style='white')

def format_plot(x, y):  
  plt.xlabel(x, fontsize=20)
  plt.ylabel(y, fontsize=20)
  
def finalize_plot(shape=(1, 1)):
  plt.gcf().set_size_inches(
    shape[0] * 1.5 * plt.gcf().get_size_inches()[1], 
    shape[1] * 1.5 * plt.gcf().get_size_inches()[1])
  plt.tight_layout()

No GPU/TPU found, falling back to CPU. (Set TF_CPP_MIN_LOG_LEVEL=0 and rerun for more info.)


In [2]:
!pip install JSAnimation

In [2]:
def createDelaunayGraph(NS, rseed, r_c, del_x):

    # This function creates a Delaunay graph of a set of points.

    # Parameters:
    #   NS: The number of points to generate.
    #   rseed: The random seed to use.
    #   r_c: The radius of the circumcircle of each edge in the graph.
    #   del_x: max noise magnitude from square lattice

    # Returns:
    #   N: The number of points in the graph.
    #   G: The graph object.
    #   X: The coordinates of the points.
    #   E: The edges of the graph.

    # Set the random seed.
    onp.random.seed(rseed)

    # Generate the points.
    xm, ym = onp.meshgrid(onp.arange(1, NS + 1), onp.arange(1, NS + 1))
    X = onp.vstack((xm.flatten(), ym.flatten())).T
    N = X.shape[0]

    # Add some noise to the points.
    X = X + del_x * 2 * (0.5 - onp.random.rand(N, 2))

    # Create the Delaunay triangulation.
    DT = Delaunay(X)

    # Get the edges of the triangulation.
    ET = onp.empty((0, 2), dtype=int)
    for T in DT.simplices:
        ET = onp.vstack((ET, [T[0], T[1]], [T[1], T[2]], [T[0], T[2]]))

    # Sort the edges.
    ET = onp.sort(ET)

    # Get the radii of the circumcircles of the edges.
    R = onp.linalg.norm(X[ET[:, 0], :] - X[ET[:, 1], :], axis=1)

    # Keep only the edges with radii less than r_c.
    EN = ET[R < r_c, :]

    # Create the adjacency matrix.
    A = onp.zeros((N, N))
    A[EN[:, 0], EN[:, 1]] = 1

    # Get the lengths of the edges.
    L = onp.linalg.norm(X[ET[:, 0], :] - X[ET[:, 1], :], axis=1)

    # Keep only the edges with lengths less than r_c.
    EL = L[R < r_c]

    # Create the graph object.
    G = nx.Graph(A)

    # Get the edges of the graph.
    E = onp.array(G.edges)

    # Get the lengths of the edges.
    L = onp.linalg.norm(X[E[:, 0], :] - X[E[:, 1], :], axis=1)

    return N, G, X, E, L

def getSurfaceNodes(G, NS):
    # Retrieve the list of nodes in the graph G
    nodes = np.array(list(G.nodes))
    # Calculate the x and y coordinates of the nodes based on the grid size NS
    x_values = nodes % NS
    y_values = nodes // NS
    # Find the nodes located on the top surface (y = NS - 1)
    top_nodes = nodes[y_values == NS - 1]
    # Find the nodes located on the bottom surface (y = 0)
    bottom_nodes = nodes[y_values == 0]
    # Find the nodes located on the left surface (x = 0)
    left_nodes = nodes[x_values == 0]
    # Find the nodes located on the right surface (x = NS - 1)
    right_nodes = nodes[x_values == NS - 1]
    # Return a dictionary with surface names as keys and node arrays as values
    return {
        'top': top_nodes,
        'bottom': bottom_nodes,
        'left': left_nodes,
        'right': right_nodes
    }

In [30]:
def make_box(R, padding):
    """
    Defines a box length

    R: position matrix
    padding: amount of space to add to the box
    """
    box_length = (np.max((np.max(R[:,0], R[:,1])) - np.min(((np.min(R[:,0], R[:,1])))))) + padding
    return box_length
    
def create_spring_constants(R,E,k_1):
    """
    Creates spring constants for each edge in the graph

    k_1: spring constant for a spring of unit length
    R: position matrix
    E: edge matrix
    """
    displacements = R[E[:, 0],:] - R[E[:, 1], :]
    distance = np.linalg.norm(displacements, axis=1)
    return (k_1/distance).reshape(-1,1), distance

@jit
def compute_distance(point1, point2):
    """
    Calculate the Euclidean distance between two points.
    """
    return np.sqrt((point1[0] - point2[0])**2 + (point1[1] - point2[1])**2)


#@jit
def constrained_force_fn(R, energy_fn, left_indices, right_indices, mask):
    """
    Calculates forces with frozen edges.

    R: position matrix
    energy_fn: energy function
    left_indices: indices of left boundary nodes
    right_indices: indices of right boundary nodes
    """
    
    
    def new_force_fn(R):
        force_fn = quantity.force(energy_fn)
        total_force = force_fn(R)
        total_force *= mask
        return total_force

    return new_force_fn


@jit
def fitness(poisson):
    """
    Constructs a fitness function based on the Poisson ratio.
    """
    return (poisson + 1)**2

@jit
def poisson_ratio(initial_horizontal, initial_vertical, final_horizontal, final_vertical):
    """
    Calculate the Poisson ratio based on average edge positions.
    
    initial_horizontal: initial horizontal edge positions
    initial_vertical: initial vertical edge positions
    final_horizontal: final horizontal edge positions
    final_vertical: final vertical edge positions
    output: Poisson ratio
    """

    delta_horizontal = final_horizontal - initial_horizontal
    delta_vertical = final_vertical - initial_vertical

    return -delta_vertical / delta_horizontal

@jit
def update_kbonds(gradients, k_bond, learning_rate = 0.01):
    """
    Updates spring constants based on gradients.

    
    """
    gradients_perpendicular = gradients - np.mean(gradients)
    gradients_normalized = gradients_perpendicular / np.max(gradients_perpendicular)
    k_bond_new = k_bond * (1 - learning_rate * gradients_normalized)

    return k_bond_new

@jit
def compute_force_norm(fire_state):
    return np.linalg.norm(fire_state.force)


def remove_zero_rows(log_dict):
    """
    Remove rows (entries) in the log dictionary that are all zeros.
    """
    for key in log_dict:
        log_dict[key] = log_dict[key][~np.all(log_dict[key] == 0.0, axis=(1, 2))]
    return log_dict

In [4]:
steps = 200
write_every = 10
perturbation = 1.0


def simulate_auxetic(R, k_bond, shift, surface_nodes, perturbation, displacement, E, bond_lengths):
    """
    Simulates the auxetic process.

    """
    # Get the surface nodes.
    top_indices = surface_nodes['top']
    bottom_indices = surface_nodes['bottom']
    left_indices = surface_nodes['left']
    right_indices = surface_nodes['right']  
    mask = np.ones(R.shape)   
    mask = mask.at[left_indices].set(0)
    mask = mask.at[right_indices].set(0)

    log_first_min = {
    'force': np.zeros((steps // write_every,) + R.shape),
    'position': np.zeros((steps // write_every,) + R.shape) 
    }

    log_second_min = {
    'force': np.zeros((steps // write_every,) + R.shape),
    'position': np.zeros((steps // write_every,) + R.shape)
    }

    def step_fn(i, state_and_log):
        """
        Minimizes the configuration at each step.

        i: step number
        state_and_log: state and log dictionary
        """
        fire_state, log = state_and_log
        
        #energy = quantity.energy(energy_fn)
        #log['energy'] = log['energy'].at[i].set(energy(fire_state.position))
        #log['energy'] = lax.cond(i % write_every == 0,
        #                         lambda e: e.at[i // write_every].set(np.array(energy_fn(fire_state.position))),
        #                         lambda e: e,
        #                         log['energy'])
        log['force'] = lax.cond(i % write_every == 0,
                                lambda p: p.at[i // write_every].set(fire_state.force),
                                lambda p: p,
                                log['force'])
        
        log['position'] = lax.cond(i % write_every == 0,
                                lambda p: p.at[i // write_every].set(fire_state.position),
                                lambda p: p,
                                log['position'])
        
        
        fire_state = fire_apply(fire_state)
        return fire_state, log
    

    # First minimization before pinching the source nodes.
    energy_fn = energy.simple_spring_bond(displacement, E, length=bond_lengths, epsilon=k_bond[:, 0])  

    fire_init, fire_apply = minimize.fire_descent(energy_fn, shift)
    fire_apply = jit(fire_apply)
    #step = jit(lambda i, state: fire_apply(state))
    fire_state = fire_init(R)
    fire_state, log_first_min = lax.fori_loop(0, steps, step_fn, (fire_state, log_first_min))
    #fire_state = lax.fori_loop(0, steps, step, fire_state)
    R_init = fire_state.position
    # Initial dimensions (before deformation)
    initial_horizontal = np.mean(R[right_indices], axis=0)[0] - np.mean(R[left_indices], axis=0)[0]
    initial_vertical = np.mean(R[top_indices], axis=0)[1] - np.mean(R[bottom_indices], axis=0)[1]

    # Shift the left edge.
    R_init = R_init.at[left_indices, 0].add(perturbation)

    # Second minimization after pinching the source nodes.
    energy_fn = energy.simple_spring_bond(displacement, E, length=bond_lengths, epsilon=k_bond[:, 0])
    force_fn = constrained_force_fn(R_init, energy_fn, left_indices, right_indices, mask)
    fire_init, fire_apply = minimize.fire_descent(force_fn, shift)
    fire_state = fire_init(R_init)
    #fire_state = lax.fori_loop(0, steps, step, fire_state)
    fire_state, log_second_min = lax.fori_loop(0, steps, step_fn, (fire_state, log_second_min))
    R_final = fire_state.position
    # Final dimensions (after deformation)
    final_horizontal = np.mean(R_final[right_indices], axis=0)[0] - np.mean(R_final[left_indices], axis=0)[0]
    final_vertical = np.mean(R_final[top_indices], axis=0)[1] - np.mean(R_final[bottom_indices], axis=0)[1]

    # Calculate the poisson ratio.
    poisson = poisson_ratio(initial_horizontal, initial_vertical, final_horizontal, final_vertical)
    fit = fitness(poisson)
    
    return fit, poisson, log_first_min, log_second_min #, traj1, traj2, step

    

In [66]:
#create graph
N,G,X,E,bond_lengths =createDelaunayGraph(10, 25, 2.0, 0.4)
R = np.array(X)
k_bond, _ = create_spring_constants(R,E,1.0)
surface_nodes = getSurfaceNodes(G, 10)
displacement, shift = space.free() #displacement = points in space, shift = small shifts of each particle
grad_f = grad(simulate_auxetic, argnums=1) 

In [26]:
surface_nodes['left']
#surface_nodes['right']

Array([ 0, 10, 20, 30, 40, 50, 60, 70, 80, 90], dtype=int64)

In [67]:
fit, poisson, traj1, traj2 = simulate_auxetic(R, k_bond, shift, surface_nodes, perturbation, displacement, E, bond_lengths)

In [9]:
poisson

Array(-0.31823721, dtype=float64)

In [63]:
traj2['position'][0]

Array([[ 1.70390077,  0.93417836],
       [ 2.17692887,  1.25127097],
       [ 3.0711199 ,  1.30609954],
       [ 3.85202501,  1.04991118],
       [ 4.9550165 ,  1.10633576],
       [ 6.07810741,  1.30956749],
       [ 7.04237533,  0.93164393],
       [ 8.27041191,  0.98342492],
       [ 9.13915909,  0.84065099],
       [10.10688432,  0.73090033],
       [ 2.01492564,  1.98679812],
       [ 2.09356155,  1.60196726],
       [ 2.98860445,  1.95275738],
       [ 4.37244019,  1.824056  ],
       [ 5.06319716,  2.05045192],
       [ 6.17463938,  1.67978058],
       [ 6.86431018,  2.03514503],
       [ 8.16815655,  1.97934479],
       [ 8.95260635,  1.80377293],
       [ 9.73732298,  1.74104444],
       [ 2.33828774,  2.88411032],
       [ 2.15259396,  2.98059698],
       [ 2.63352618,  2.69343924],
       [ 4.16365452,  2.99009926],
       [ 5.32903806,  2.88662662],
       [ 6.29406355,  2.78681137],
       [ 7.3386062 ,  3.13516493],
       [ 7.85611874,  2.99262949],
       [ 8.8758831 ,

In [ ]:
%timeit grad_f(R, k_bond, shift, surface_nodes, perturbation, displacement, E, bond_lengths)

In [51]:
max_steps = 1000
write_every = 10
perturbation = 0.1
tolerance = 1e-6  # Set the desired tolerance for the minimization.


def simulate_auxetic(R, k_bond, shift, surface_nodes, perturbation, displacement, E, bond_lengths):
    """
    Simulates the auxetic process.

    """
    # Get the surface nodes.
    top_indices = surface_nodes['top']
    bottom_indices = surface_nodes['bottom']
    left_indices = surface_nodes['left']
    right_indices = surface_nodes['right']
    mask = np.ones(R.shape)   
    mask = mask.at[left_indices].set(0)
    mask = mask.at[right_indices].set(0)
    
    log_first_min = {
    'force': np.zeros((max_steps // write_every,) + R.shape),
    'position': np.zeros((max_steps // write_every,) + R.shape) 
    }

    log_second_min = {
    'force': np.zeros((max_steps // write_every,) + R.shape),
    'position': np.zeros((max_steps // write_every,) + R.shape)
    }

    def step_fn(i, state_and_log):
        """
        Minimizes the configuration at each step.

        i: step number
        state_and_log: state and log dictionary
        """
        fire_state, log = state_and_log
        
        #energy = quantity.energy(energy_fn)
        #log['energy'] = log['energy'].at[i].set(energy(fire_state.position))
        #log['energy'] = lax.cond(i % write_every == 0,
        #                         lambda e: e.at[i // write_every].set(np.array(energy_fn(fire_state.position))),
        #                         lambda e: e,
        #                         log['energy'])
        log['force'] = lax.cond(i % write_every == 0,
                                lambda p: p.at[i // write_every].set(fire_state.force),
                                lambda p: p,
                                log['force'])
        
        log['position'] = lax.cond(i % write_every == 0,
                                lambda p: p.at[i // write_every].set(fire_state.position),
                                lambda p: p,
                                log['position'])
        
        
        fire_state = fire_apply(fire_state)
        return fire_state, log

    # First minimization before pinching the source nodes.
    energy_fn = energy.simple_spring_bond(displacement, E, length=bond_lengths, epsilon=k_bond[:, 0])  

    fire_init, fire_apply = minimize.fire_descent(energy_fn, shift)
    fire_apply = jit(fire_apply)
    #step = jit(lambda i, state: fire_apply(state))
    fire_state = fire_init(R)
    fire_state, log_first_min = lax.fori_loop(0, steps, step_fn, (fire_state, log_first_min))
    #fire_state = lax.fori_loop(0, steps, step, fire_state)
    R_init = fire_state.position
    # Initial dimensions (before deformation)
    initial_horizontal = np.mean(R[right_indices], axis=0)[0] - np.mean(R[left_indices], axis=0)[0]
    initial_vertical = np.mean(R[top_indices], axis=0)[1] - np.mean(R[bottom_indices], axis=0)[1]

    # Shift the left edge.
    R_init = R_init.at[left_indices, 0].add(perturbation)

    # Second minimization after pinching the source nodes.
    energy_fn = energy.simple_spring_bond(displacement, E, length=bond_lengths, epsilon=k_bond[:, 0])
    force_fn = constrained_force_fn(R_init, energy_fn, left_indices, right_indices, mask)
    fire_init, fire_apply = minimize.fire_descent(force_fn, shift, 0.1)
    fire_state = fire_init(R_init)
    previous_force_norm = compute_force_norm(fire_state)
    current_force_norm = np.inf  # Initializing to a high value
    #fire_state = lax.fori_loop(0, steps, step, fire_state)
    #fire_state, log_second_min = lax.fori_loop(0, steps, step_fn, (fire_state, log_second_min))
    state_and_log = (fire_state, log_second_min)
    step = 0
    while abs(previous_force_norm - current_force_norm) > tolerance:
        step += 1
        fire_state, log = state_and_log
        
        #energy = quantity.energy(energy_fn)
        #log['energy'] = log['energy'].at[i].set(energy(fire_state.position))
        #log['energy'] = lax.cond(i % write_every == 0,
        #                         lambda e: e.at[i // write_every].set(np.array(energy_fn(fire_state.position))),
        #                         lambda e: e,
        #                         log['energy'])
        log['force'] = lax.cond(step % write_every == 0,
                                lambda p: p.at[step // write_every].set(fire_state.force),
                                lambda p: p,
                                log['force'])
        
        log['position'] = lax.cond(step % write_every == 0,
                                lambda p: p.at[step // write_every].set(fire_state.position),
                                lambda p: p,
                                log['position'])
        
        
        fire_state = fire_apply(fire_state)
        state_and_log = (fire_state, log)
        previous_force_norm = current_force_norm
        current_force_norm = compute_force_norm(fire_state)

        #    Optional: To prevent infinite loops, break if the number of steps exceeds a limit
        if step > max_steps:
            break

    log_first_min = remove_zero_rows(log_first_min)
    log_second_min = remove_zero_rows(log_second_min)
    R_final = fire_state.position
    # Final dimensions (after deformation)
    final_horizontal = np.mean(R_final[right_indices], axis=0)[0] - np.mean(R_final[left_indices], axis=0)[0]
    final_vertical = np.mean(R_final[top_indices], axis=0)[1] - np.mean(R_final[bottom_indices], axis=0)[1]

    # Calculate the poisson ratio.
    poisson = poisson_ratio(initial_horizontal, initial_vertical, final_horizontal, final_vertical)
    fit = fitness(poisson)
    
    return fit#, poisson, log_first_min, log_second_min #, traj1, traj2, step

    

In [52]:
#create graph
N,G,X,E,bond_lengths =createDelaunayGraph(10, 25, 2.0, 0.4)
R = np.array(X)
k_bond, _ = create_spring_constants(R,E,1.0)
surface_nodes = getSurfaceNodes(G, 10)
displacement, shift = space.free() #displacement = points in space, shift = small shifts of each particle
grad_f = grad(simulate_auxetic, argnums=1) 

In [47]:
fit, poisson, traj1, traj2 = simulate_auxetic(R, k_bond, shift, surface_nodes, perturbation, displacement, E, bond_lengths)

In [48]:
print(poisson)

0.17128190690185713


In [23]:
%timeit  fit, poisson, traj1, traj2 = simulate_auxetic(R, k_bond, shift, surface_nodes, perturbation, displacement, E, bond_lengths)

8.71 s ± 303 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


In [44]:
traj1['force'][20]

Array([[-1.54748385e-14,  2.69628353e-13],
       [ 1.74322732e-13,  2.80123985e-13],
       [-3.76359341e-13, -2.12098938e-13],
       [-6.35905770e-13, -1.89242621e-13],
       [-4.88015672e-13, -6.59473983e-14],
       [ 2.64575554e-13,  4.12578609e-14],
       [ 2.16345682e-14,  1.09954034e-14],
       [-6.89641453e-14,  1.38117102e-13],
       [ 1.44824434e-13,  8.93018415e-14],
       [ 1.42701027e-14, -4.13215627e-13],
       [-3.47170800e-13,  1.69671293e-13],
       [-8.36815155e-14,  1.62186461e-13],
       [ 1.88180899e-13,  1.40584412e-13],
       [-1.21431025e-14, -2.57370419e-13],
       [-1.34638691e-13, -3.23359265e-14],
       [-1.10488618e-13, -3.65597416e-13],
       [-1.12996038e-13,  2.23111562e-13],
       [ 1.34208364e-13, -1.09907066e-13],
       [ 6.32003755e-14, -1.11359918e-13],
       [ 1.47455034e-13,  2.94212754e-13],
       [ 3.02343462e-13,  2.12314831e-13],
       [ 4.13615358e-13,  2.01768828e-14],
       [ 1.00621961e-13,  3.66255979e-14],
       [-2.

In [49]:
ms = 30
R_plt = onp.array(traj2['position'][-1])

plt.plot(R_plt[:N, 0], R_plt[:N, 1], 'o', markersize=ms * 0.5)

# Plotting bonds
for bond in E:
    point1 = R_plt[bond[0]]
    point2 = R_plt[bond[1]]
    plt.plot([point1[0], point2[0]], [point1[1], point2[1]], c='black')  # Using black for bond color


plt.xlim([0, np.max(R_plt[:, 0])])
plt.ylim([0, np.max(R_plt[:, 1])])

plt.axis('on')

finalize_plot((1, 1))

<IPython.core.display.Javascript object>

In [50]:
%matplotlib notebook
from matplotlib.animation import FuncAnimation
from JSAnimation.IPython_display import display_animation
from IPython.display import HTML

# Set style
sns.set_style(style='white')

# Define the init function, which sets up the plot
def init():
    plt.xlim([0, np.max(traj2['position'][:, :, 0])])
    plt.ylim([0, np.max(traj2['position'][:, :, 1])])
    plt.axis('on')
    return plt

# Define the update function, which is called for each frame
def update(frame):
    plt.clf()  # Clear the current figure
    R_plt = traj2['position'][frame]
    plt.plot(R_plt[:N, 0], R_plt[:N, 1], 'o', markersize=ms * 0.5)

    # Plotting bonds
    for bond in E:
        point1 = R_plt[bond[0]]
        point2 = R_plt[bond[1]]
        plt.plot([point1[0], point2[0]], [point1[1], point2[1]], c='black')  # Using black for bond color
    return plt

# Create the animation
ani = FuncAnimation(plt.figure(), update, frames=range(len(traj2['position'])), init_func=init, blit=False)

# Display the animation
HTML(ani.to_jshtml())

<IPython.core.display.Javascript object>

In [53]:
opt_steps = 200
k_temp = k_bond
for i in range(opt_steps):
    net_fitness = simulate_auxetic(R, k_temp, shift, surface_nodes, perturbation, displacement, E, bond_lengths)
    gradients = grad_f(R, k_temp, shift, surface_nodes, perturbation, displacement, E, bond_lengths)
    k_temp = update_kbonds(gradients, k_temp)
    print(i, np.max(gradients), net_fitness)

0 0.02380444290600785 1.3719013054356508
1 0.023945835823195684 1.369113658519334
2 0.024087962539826303 1.3663643162550831
3 0.02479593837675802 1.3634325920069008
4 0.024950359908713776 1.3608241111635369
5 0.025105511189232304 1.3582497817942893
6 0.025261380058567352 1.3557087316997618
7 0.024514241194614678 1.3536655240324627
8 0.024660184779743525 1.3510826127489695
9 0.024806684844292538 1.3485326524937085
10 0.024953730643821153 1.346014808954247
11 0.025101311683140386 1.3435282798953652
12 0.025249417698570583 1.341072293406917
13 0.02539803864231406 1.3386461062834718
14 0.02554716466805639 1.3362490025197242
15 0.02569678611745009 1.3338802919107486
16 0.02648121009620361 1.3312127954337754
17 0.026636423771028036 1.3289676676397668
18 0.02679221201888232 1.326747703549361
19 0.026948564101875277 1.3245523574012177
20 0.027050203367121425 1.3223811353805461
21 0.027206809333223357 1.3202299596764446
22 0.027363954430019776 1.3181019128829423
23 0.02752162861373357 1.3159965

: 

In [17]:
import plotly.graph_objs as go
from plotly.subplots import make_subplots

# Convert the trajectory to a NumPy array
trajectory_array = np.array(traj_shifted)

# Create a subplot for the scatter plot
fig = make_subplots(rows=1, cols=1, specs=[[{'type': 'scatter'}]], print_grid=False)

# Create a scatter plot using Plotly
trace = go.Scatter(x=trajectory_array[:, 0], y=trajectory_array[:, 1], mode='markers')
fig.add_trace(trace)

# Create and add slider
steps = []
for i, frame in enumerate(trajectory_array):
    step = dict(
        method="update",
        args=[
            {"x": [frame[:, 0]], "y": [frame[:, 1]]},
        ],
        label=str(i),
    )
    steps.append(step)

slider = dict(steps=steps, active=0, pad={"t": 50}, currentvalue={"prefix": "Frame: "})

fig.update_layout(sliders=[slider])

# Update the layout
fig.update_layout(
    width=600,
    height=600,
    xaxis=dict(title='X', showgrid=False),
    yaxis=dict(title='Y', showgrid=False),
    plot_bgcolor='rgba(255, 255, 255, 1)', # White background
    margin=dict(l=50, r=50, b=50, t=50) # Adjust margin if needed
)

fig.show()
